In [1]:
import torch
import torch.nn as nn
import torch.nn.functional as F

import numpy as np

import librosa

In [2]:
import numpy as np
import librosa

In [3]:
#from tensorflow.python.client import device_lib

In [4]:
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Dense, Dropout, Activation, LSTM, RepeatVector, TimeDistributed, ELU, ReLU, Conv1D, Conv1DTranspose 
from tensorflow.keras.optimizers import Adam
from tensorflow.keras.models import load_model
import tensorflow as tf

In [5]:
import os

In [6]:
import itertools
from itertools import chain, repeat, islice

def pad_infinite(iterable, padding=None):
   return chain(iterable, repeat(padding))

def pad(iterable, size, padding=None):
   return islice(pad_infinite(iterable, padding), size)


In [7]:
#ADD street, buses and outdoor noise to the clean audio files:

mixed_audios = []
clean_audios = []
sr = []
for filename in os.listdir("/users/rohanchitte/downloads/clean_testset_wav/"):
    print(filename)
    path = "/users/rohanchitte/downloads/clean_testset_wav/" + filename
    cleanaudio, sample_rate1 = librosa.load(path, mono=True, sr=None, offset=0)
    cleanaudio = cleanaudio.tolist()

    for filename2 in os.listdir("/users/rohanchitte/downloads/Environment/"):
        print(filename2)
        path2 = "/users/rohanchitte/downloads/Environment/" + filename2
        
        noiseaudio, sample_rate2 = librosa.load(path2, mono=True, sr=None, offset=0)
        noiseaudio = noiseaudio.tolist()


        if len(cleanaudio) > len(noiseaudio):
            leng = len(cleanaudio)
            x = list(pad(noiseaudio, leng, 0))
            x = np.array(x)
            cleanaudio = np.array(cleanaudio)
            x = (x + cleanaudio)/2
            x = x[:500000]
            x = x.tolist()
            cleanaudio = cleanaudio.tolist()
            mixed_audios.append(x)
            clean_audios.append(cleanaudio)
            samplerate = int((sample_rate1+sample_rate2)/2)
            sr.append(samplerate)
        else:
            leng = len(noiseaudio)
            x = list(pad(cleanaudio, leng, 0))
            x = np.array(x)
            noiseaudio = np.array(noiseaudio)
            x = (x + noiseaudio)/2
            x = x[:500000]
            x = x.tolist()
           # cleanaudio = cleanaudio.tolist()
            mixed_audios.append(x)
            clean_audios.append(cleanaudio)
            samplerate = int((sample_rate1+sample_rate2)/2)
            sr.append(samplerate)


p232_009.wav
street.wav
buses.wav
outdoor.wav
p232_007.wav
street.wav
buses.wav
outdoor.wav
p232_006.wav
street.wav
buses.wav
outdoor.wav
p232_010.wav
street.wav
buses.wav
outdoor.wav
p232_005.wav
street.wav
buses.wav
outdoor.wav
p232_001.wav
street.wav
buses.wav
outdoor.wav
p232_002.wav
street.wav
buses.wav
outdoor.wav
p232_003.wav
street.wav
buses.wav
outdoor.wav


# Data Preprocessing

Convert the vectors into equal lenghts and further convert it into a tensor for deep learning training

In [8]:
#padding noise audios
import itertools
noisy_audios_padded = zip(*itertools.zip_longest(*mixed_audios, fillvalue=0))
noisy_audios_padded = list(noisy_audios_padded)

noisy_tensor = tf.convert_to_tensor(noisy_audios_padded, dtype=tf.float32)


In [9]:
noisy_tensor.shape

TensorShape([24, 500000])

In [10]:
#padding clean audios
import itertools
clean_audios_padded = zip(*itertools.zip_longest(*clean_audios, fillvalue=0))
clean_audios_padded = list(clean_audios_padded)

clean_tensor = tf.convert_to_tensor(clean_audios_padded, dtype=tf.float32)

In [11]:
shapes =  [noisy_tensor.shape[1],clean_tensor.shape[1]]
shapes.sort()
length = shapes[-1]
length

500000

In [12]:
#Converting noise and clean audios to have the same vector length
if noisy_tensor.shape[1] > clean_tensor.shape[1]:
    clean_audios_padded_matched = []
    for i in clean_audios_padded:
        x = list(pad(i, length, 0))
        clean_audios_padded_matched.append(x)

    clean_tensor = tf.convert_to_tensor(clean_audios_padded_matched, dtype=tf.float32)
elif noisy_tensor.shape[1] < clean_tensor.shape[1]:
    noisy_audios_padded_matched = []
    for i in noisy_audios_padded:
        x = list(pad(i, length, 0))
        noisy_audios_padded_matched.append(x)

    noisy_tensor = tf.convert_to_tensor(noisy_audios_padded_matched, dtype=tf.float32)
else:
    pass

In [13]:
print(clean_tensor.shape)
print(noisy_tensor.shape)

(24, 500000)
(24, 500000)


In [14]:
#Reshaping the tensor to fit the LSTM model
clean_tensor_reshape = tf.reshape(clean_tensor, [length, -1, 1])
noisy_tensor_reshape = tf.reshape(noisy_tensor, [length, -1, 1])

In [15]:
print(clean_tensor_reshape.shape)
print(noisy_tensor_reshape.shape)

(500000, 24, 1)
(500000, 24, 1)


In [16]:
#Example of the noise audio
import IPython.display as ipd
display(ipd.Audio(noisy_tensor[0], rate=sr[0]));

In [17]:
#Example of the clean audio
import IPython.display as ipd
display(ipd.Audio(clean_tensor[2], rate=sr[0]));

# Model Training

In [18]:
model = Sequential()

model.add(LSTM(10, activation='relu', input_shape=(24,1)))

model.add(RepeatVector(24))

model.add(LSTM(10, activation='relu', return_sequences=True))
model.add(TimeDistributed(Dense(1)))

model.compile(optimizer='adam', loss='mse')


In [19]:
model.summary()

Model: "sequential"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
lstm (LSTM)                  (None, 10)                480       
_________________________________________________________________
repeat_vector (RepeatVector) (None, 24, 10)            0         
_________________________________________________________________
lstm_1 (LSTM)                (None, 24, 10)            840       
_________________________________________________________________
time_distributed (TimeDistri (None, 24, 1)             11        
Total params: 1,331
Trainable params: 1,331
Non-trainable params: 0
_________________________________________________________________


In [20]:
epoch = 15
history = model.fit(noisy_tensor_reshape, clean_tensor_reshape, verbose = 1, validation_split=0.3, epochs = epoch)  

Epoch 1/15
10938/10938 [==============================] - 328s 30ms/step - loss: 0.0017 - val_loss: 0.0016
Epoch 2/15
10938/10938 [==============================] - 267s 24ms/step - loss: 0.0014 - val_loss: 0.0013
Epoch 3/15
10938/10938 [==============================] - 283s 26ms/step - loss: 0.0013 - val_loss: 0.0013
Epoch 4/15
10938/10938 [==============================] - 275s 25ms/step - loss: 0.0013 - val_loss: 0.0013
Epoch 5/15
10938/10938 [==============================] - 273s 25ms/step - loss: 0.0013 - val_loss: 0.0012
Epoch 6/15
10938/10938 [==============================] - 270s 25ms/step - loss: 0.0012 - val_loss: 0.0013
Epoch 7/15
10938/10938 [==============================] - 274s 25ms/step - loss: 0.0012 - val_loss: 0.0012
Epoch 8/15
10938/10938 [==============================] - 340s 31ms/step - loss: 0.0012 - val_loss: 0.0012
Epoch 9/15
10938/10938 [==============================] - 342s 31ms/step - loss: 0.0012 - val_loss: 0.0012
Epoch 10/15
10938/10938 [============

# Model predictions

In [21]:
#Converting predictions to the original shape
predictions = model.predict(noisy_tensor_reshape)
predictions_reshape = tf.reshape(predictions, [ -1,length]) 

In [22]:
#Predicted audio file 1
import IPython.display as ipd
display(ipd.Audio(predictions_reshape[0], rate=sr[0]));

In [23]:
#Noisy audio file 1
import IPython.display as ipd
display(ipd.Audio(noisy_tensor[0], rate=sr[0]));

# Export Clean audios as audio wav files

In [24]:
import soundfile as sf
for i in range(24):
    istr = str(i)
    sf.write('clean'+istr+'.wav', clean_tensor[i], sr[0])

# Export Predictions of clean audios as audio wav files

In [25]:
import soundfile as sf
for i in range(24):
    istr = str(i)
    sf.write('prediction'+istr+'.wav', predictions_reshape[i], sr[0])

# Export Noisy audos as audio wav files

In [26]:
import soundfile as sf
for i in range(24):
    istr = str(i)
    sf.write('noise'+istr+'.wav', noisy_tensor[i], sr[0])

# Speech Recognition (Audio to text)

In [29]:
import speech_recognition as sr
r = sr.Recognizer()

In [30]:
# open the file
predictedtexts = []
for i in range(24):
    print(i)
    istr = str(i)
    path='prediction'+istr+'.wav'
    print(path)
    r = sr.Recognizer()
    with sr.AudioFile(path) as source:
        # listen for the data (load audio to memory)
        audio_data = r.record(source, duration=8)
        # recognize (convert from speech to text)
        text = r.recognize_google(audio_data)
        print(text)
        predictedtexts.append(text)

0
prediction0.wav
there is according to Legend a boiling pot of gold at one end
1
prediction1.wav
there is according to Legend a boiling pot of gold at one end
2
prediction2.wav
there is according to Legend a boiling pot of gold at one end
3
prediction3.wav
the rainbow is a division of white light into many beautiful colours
4
prediction4.wav
the rainbow is a division of white light into many beautiful colours
5
prediction5.wav
the rainbow is a division of white light into many beautiful colours
6
prediction6.wav
when the sunlight strikes raindrops in the air the act as a prism and former rainbow
7
prediction7.wav
when the sunlight strikes raindrops in the air the act as a prism and former rainbow
8
prediction8.wav
when the sunlight strikes raindrops in the air the act as a prism and former rainbow
9
prediction9.wav
people look but no one ever finds it
10
prediction10.wav
people look but no one ever finds it
11
prediction11.wav
people look but no one ever finds it
12
prediction12.wav
s

In [31]:
# open the file
cleantexts = []
for i in range(24):
    print(i)
    istr = str(i)
    path='clean'+istr+'.wav'
    print(path)
    r = sr.Recognizer()
    with sr.AudioFile(path) as source:
        # listen for the data (load audio to memory)
        audio_data = r.record(source, duration=8)
        # recognize (convert from speech to text)
        text = r.recognize_google(audio_data)
        print(text)
        cleantexts.append(text)

0
clean0.wav
there is according to Legend a boiling pot of gold at one end
1
clean1.wav
there is according to Legend a boiling pot of gold at one end
2
clean2.wav
there is according to Legend a boiling pot of gold at one end
3
clean3.wav
the rainbow is a division of white light into many beautiful colours
4
clean4.wav
the rainbow is a division of white light into many beautiful colours
5
clean5.wav
the rainbow is a division of white light into many beautiful colours
6
clean6.wav
when the sunlight strikes raindrops in the air the act as a prism and former rainbow
7
clean7.wav
when the sunlight strikes raindrops in the air the act as a prism and former rainbow
8
clean8.wav
when the sunlight strikes raindrops in the air the act as a prism and former rainbow
9
clean9.wav
people look but no one ever finds it
10
clean10.wav
people look but no one ever finds it
11
clean11.wav
people look but no one ever finds it
12
clean12.wav
she can scoop these things into 3 red bags and we will go meet her

In [32]:
# open the file
noisytexts = []
for i in range(24):
    print(i)
    istr = str(i)
    path='noise'+istr+'.wav'
    print(path)
    r = sr.Recognizer()
    with sr.AudioFile(path) as source:
        # listen for the data (load audio to memory)
        audio_data = r.record(source, duration=8)
        # recognize (convert from speech to text)
        text = r.recognize_google(audio_data)
        print(text)
        noisytexts.append(text)

0
noise0.wav
there is a garden to Legend a boiling pot of gold at one end
1
noise1.wav
there is according to Legend a boiling pot of gold at one end
2
noise2.wav
there is a garden to Legend a boiling pot of gold at one end
3
noise3.wav
the rainbow is a division of white light into many beautiful colours
4
noise4.wav
the rainbow is a division of white light into many beautiful colours
5
noise5.wav
the rainbow is a division of white light into many beautiful colours
6
noise6.wav
when the sunlight strikes raindrops in the air the act as a prism and form a rainbow
7
noise7.wav
when the sunlight strikes raindrops in the air the act as a prism and former rainbow
8
noise8.wav
when the sunlight strikes raindrops in the air the act as a prism and former rainbow
9
noise9.wav
people look but no one ever finds it
10
noise10.wav
people look but no one ever finds it
11
noise11.wav
people look but no one ever playing it
12
noise12.wav
she can scoop these things into 3 red bags and we will go meet her

# WER calculation

In [38]:
#Check wer between clean and predicted text
from jiwer import wer
errors = []
for i in range(24):
    error = wer(cleantexts, predictedtexts)
    errors.append(error)
print(np.mean(errors))

0.0


In [39]:
#Check wer between clean and noisy text
from jiwer import wer
errors = []
for i in range(24):
    error = wer(cleantexts, noisytexts)
    errors.append(error)
print(np.mean(errors))

0.08250825082508251


In [40]:
#Check wer between predicted and noisy text
from jiwer import wer
errors = []
for i in range(24):
    error = wer(predictedtexts, noisytexts)
    errors.append(error)
print(np.mean(errors))

0.08250825082508251
